Based on sergiolucero's code here: https://gist.github.com/sergiolucero/e0a6dd13494f139acd968e231906aef2
and Bert Carremans' code here: https://towardsdatascience.com/visualizing-air-pollution-with-folium-maps-4ce1a1880677

A follow up to my map of Covid-19 in Italy: https://github.com/seantibbitts/mapping-Covid-19-in-Italy/blob/master/Mapping%20Covid-19%20in%20Italy.ipynb
(View on NBViewer here: https://nbviewer.jupyter.org/github/seantibbitts/mapping-Covid-19-in-Italy/blob/master/Mapping%20Covid-19%20in%20Italy.ipynb)

In [1]:
import pandas as pd
import folium, branca
from folium.plugins import TimestampedGeoJson
from folium import Popup
from bs4 import BeautifulSoup
import requests
from datetime import datetime
from urllib.error import HTTPError

### The data is stored on Github in datestamped CSV files. Create a list of dates to pull from.

In [2]:
dates = pd.date_range(start='01-22-2020', end = datetime.now()).to_list()

In [25]:
df = pd.DataFrame()

### Download each CSV.

In [26]:
for date in dates:
    date_str = date.strftime('%m-%d-%Y')
    path = f'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/{date_str}.csv'
    try:
        download_df = pd.read_csv(path)\
        .rename(columns = {'Province_State':'Province/State','Country_Region':'Country/Region',
                           'Last_Update':'Last Update','Lat':'Latitude','Long_':'Longitude'})
        df = df.append(download_df)
    except HTTPError as e:
        pass

In [29]:
df[df['Active'].notnull()]

Province/State Country/Region          Last Update  Confirmed  Deaths  \
0     South Carolina             US  2020-03-23 23:19:34        1.0     0.0   
1          Louisiana             US  2020-03-23 23:19:34        1.0     0.0   
2           Virginia             US  2020-03-23 23:19:34        1.0     0.0   
3              Idaho             US  2020-03-23 23:19:34       13.0     0.0   
4               Iowa             US  2020-03-23 23:19:34        1.0     0.0   
...              ...            ...                  ...        ...     ...   
3412             NaN     Uzbekistan  2020-03-24 23:37:15       50.0     0.0   
3413             NaN      Venezuela  2020-03-24 23:37:15       84.0     0.0   
3414             NaN        Vietnam  2020-03-24 23:37:15      134.0     0.0   
3415             NaN         Zambia  2020-03-24 23:37:15        3.0     0.0   
3416             NaN       Zimbabwe  2020-03-24 23:37:15        3.0     1.0   

      Recovered   Latitude   Longitude     FIPS     Admin2  Active  \
0           0.0  34.223334  -82.461707  45001.0  Abbeville     0.0   
1           0.0  30.295065  -92.414197  22001.0     Acadia     0.0   
2           0.0  37.767072  -75.632346  51001.0   Accomack     0.0   
3           0.0  43.452658 -116.241552  16001.0        Ada     0.0   
4           0.0  41.330756  -94.471059  19001.0      Adair     0.0   
...         ...        ...         ...      ...        ...     ...   
3412        0.0  41.377491   64.585262      NaN        NaN    50.0   
3413       15.0   6.423800  -66.589700      NaN        NaN    69.0   
3414       17.0  14.058324  108.277199      NaN        NaN   117.0   
3415        0.0 -13.133897   27.849332      NaN        NaN     3.0   
3416        0.0 -19.015438   29.154857      NaN        NaN     2.0   

                       Combined_Key  
0     Abbeville, South Carolina, US  
1             Acadia, Louisiana, US  
2            Accomack, Virginia, US  
3                    Ada, Idaho, US  
4                   Adair, Iowa, US  
...                             ...  
3412                     Uzbekistan  
3413                      Venezuela  
3414                        Vietnam  
3415                         Zambia  
3416                       Zimbabwe  

[6832 rows x 12 columns]

In [51]:
df0 = df.drop_duplicates().copy()

### Some of the location data is empty. Attempt to fill it by grouping by province and region and taking the max of the latitude and longitude.

In [52]:
# Start by creating a non-null primary key that can be used in the groupby
df0['admin_province_country'] = df0['Admin2'].str.cat([df0['Province/State'],df0['Country/Region']], na_rep = '')

In [53]:
# Take the max
df_max = df0.groupby('admin_province_country')[['Latitude','Longitude']].max().reset_index()

In [54]:
# Merge the coordinates back onto the dataframe
df1 = pd.merge(df0, df_max, how = 'left', on = 'admin_province_country')

In [55]:
# Create new latitude and longitude columns by filling NAs with the new values
df1['Latitude'] = df1['Latitude_x'].fillna(df1['Latitude_y'])
df1['Longitude'] = df1['Longitude_x'].fillna(df1['Longitude_y'])

In [56]:
# Limit dataframe to rows where the location data is not null
df2 = df1[df1['Latitude'].notnull() & df1['Longitude'].notnull()].copy()

### The 'Last Update' column is type object, not date. Transform into a datetime.

In [57]:
df2['Last Update Date'] = pd.to_datetime(df2['Last Update'], yearfirst=True)

### Resample dates for each location to be daily

In [73]:
# Dataframe is not unique on date and location, so take last in each group'
# Then resample
df2_1 = df2.sort_values(['Confirmed','Deaths','Recovered'])\
.groupby(['Last Update Date','admin_province_country'], as_index = False).last()\
.set_index('Last Update Date').groupby('admin_province_country', as_index = False).resample('D').ffill()\
.reset_index('Last Update Date').reset_index(drop = True)

### Set the location (chose Italy just because)

In [74]:
location = (43.0000,12.0000)

In [75]:
df3 = df2_1[(df2_1['Confirmed']>0)|(df2_1['Deaths']>0)|(df2_1['Recovered']>0)].copy()

### Define colormaps for the Confirmed, Deaths and Recovered columns

In [76]:
colormap_confirmed = branca.colormap.linear.YlOrRd_03.scale(0, df3['Confirmed'].max())
colormap_deaths = branca.colormap.LinearColormap(['#9fc8e1','#2171b5']).scale(0, df3['Deaths'].max())
colormap_recovered = branca.colormap.linear.RdYlGn_03.scale(0, df3['Recovered'].max())

### Compile feature lists for Confirmed, Deaths and Recovered columns.
#### Sort by value so that higher rates show up on top in the maps.

In [77]:
features_confirmed = []

In [78]:
for _, row in df3[df3['Confirmed']>0].sort_values('Confirmed').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_confirmed(row['Confirmed'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_confirmed(row['Confirmed']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_confirmed.append(feature)

In [79]:
features_deaths = []

In [80]:
for _, row in df3[df3['Deaths']>0].sort_values('Deaths').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_deaths(row['Deaths'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_deaths(row['Deaths']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_deaths.append(feature)

In [81]:
features_recovered = []

In [82]:
for _, row in df3[df3['Recovered']>0].sort_values('Recovered').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_recovered(row['Recovered'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_recovered(row['Recovered']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            },
            'recovered':row['Recovered']
        }
    }
    features_recovered.append(feature)

### Initialize the map objects and add colorbars at the top

In [83]:
fm_confirmed = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=800, height=400)\
.add_child(colormap_confirmed)

In [95]:
fm_deaths = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=800, height=400)\
.add_child(colormap_deaths)

In [92]:
fm_recovered = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=800, height=400)\
.add_child(colormap_recovered)

### Feed the features lists into TimestampedGeoJson objects and add to maps

In [86]:
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_confirmed}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1D'
).add_to(fm_confirmed)

In [96]:
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_deaths}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1M'
).add_to(fm_deaths)

In [93]:
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_recovered}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1M'
).add_to(fm_recovered)

## Time Series Map of Confirmed Covid-19 Cases

In [89]:
fm_confirmed

## Time Series Map of Covid-19 Deaths

In [97]:
fm_deaths

## Time Series Map of Recovered Covid-19 Cases

In [94]:
fm_recovered